In [1]:
import altair as alt
import polars as pl
from pathlib import Path
from vega_datasets import data
import geopandas as gpd
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [2]:
# Load data set
df = pl.read_csv("data/FoodImports.csv", ignore_errors=True)

# Clean data set
df_clean = (
    df
    .filter(
        ~pl.col("Country").str.contains("WORLD|Rest of World|Quantity")
        & (pl.col("UOM") == "Million $")
        & pl.col("FoodValue").is_not_null()
        & pl.col("YearNum").is_not_null()
    )
    .filter(~pl.col("Commodity").str.starts_with("Total"))
)

df_clean

shape: (9_490, 8)
┌─────────────┬─────────────┬───────────┬───────────┬────────────┬───────────┬─────────┬───────────┐
│ Commodity   ┆ Country     ┆ UOM       ┆ Category  ┆ SubCategor ┆ RowNumber ┆ YearNum ┆ FoodValue │
│ ---         ┆ ---         ┆ ---       ┆ ---       ┆ y          ┆ ---       ┆ ---     ┆ ---       │
│ str         ┆ str         ┆ str       ┆ str       ┆ ---        ┆ i64       ┆ i64     ┆ f64       │
│             ┆             ┆           ┆           ┆ str        ┆           ┆         ┆           │
╞═════════════╪═════════════╪═══════════╪═══════════╪════════════╪═══════════╪═════════╪═══════════╡
│ Bovine      ┆ CANADA      ┆ Million $ ┆ Animals   ┆ Foods      ┆ 6         ┆ 1999    ┆ 639.0     │
│ animals,    ┆             ┆           ┆           ┆            ┆           ┆         ┆           │
│ live        ┆             ┆           ┆           ┆            ┆           ┆         ┆           │
│ Bovine      ┆ MEXICO      ┆ Million $ ┆ Animals   ┆ Foods      ┆ 7         ┆ 1999    ┆ 292.1     │
│ animals,    ┆             ┆           ┆           ┆            ┆           ┆         ┆           │
│ live        ┆             ┆           ┆           ┆            ┆           ┆         ┆           │
│ Swine, live ┆ CANADA      ┆ Million $ ┆ Animals   ┆ Foods      ┆ 10        ┆ 1999    ┆ 216.1     │
│ Sheep and   ┆ CANADA      ┆ Million $ ┆ Animals   ┆ Foods      ┆ 13        ┆ 1999    ┆ 5.3       │
│ goats, live ┆             ┆           ┆           ┆            ┆           ┆         ┆           │
│ Live        ┆ CANADA      ┆ Million $ ┆ Animals   ┆ Foods      ┆ 16        ┆ 1999    ┆ 16.5      │
│ poultry     ┆             ┆           ┆           ┆            ┆           ┆         ┆           │
│ …           ┆ …           ┆ …         ┆ …         ┆ …          ┆ …         ┆ …       ┆ …         │
│ Liquors and ┆ CANADA      ┆ Million $ ┆ Beverages ┆ Foods      ┆ 45        ┆ 2024    ┆ 622.7     │
│ liqueurs    ┆             ┆           ┆           ┆            ┆           ┆         ┆           │
│ Liquors and ┆ NETHERLANDS ┆ Million $ ┆ Beverages ┆ Foods      ┆ 46        ┆ 2024    ┆ 351.2     │
│ liqueurs    ┆             ┆           ┆           ┆            ┆           ┆         ┆           │
│ Liquors and ┆ IRELAND     ┆ Million $ ┆ Beverages ┆ Foods      ┆ 47        ┆ 2024    ┆ 325.2     │
│ liqueurs    ┆             ┆           ┆           ┆            ┆           ┆         ┆           │
│ Liquors and ┆ ITALY       ┆ Million $ ┆ Beverages ┆ Foods      ┆ 48        ┆ 2024    ┆ 245.2     │
│ liqueurs    ┆             ┆           ┆           ┆            ┆           ┆         ┆           │
│ Liquors and ┆ SWEDEN      ┆ Million $ ┆ Beverages ┆ Foods      ┆ 49        ┆ 2024    ┆ 148.4     │
│ liqueurs    ┆             ┆           ┆           ┆            ┆           ┆         ┆           │
└─────────────┴─────────────┴───────────┴───────────┴────────────┴───────────┴─────────┴───────────┘

In [3]:
"""
Visualization 1: Total U.S. Food Imports Over Time

This chart introduces the overall trajectory of U.S. food import value across the available years in the dataset. 
After cleaning the data to remove world-level aggregates and non-monetary units, the line represents the sum of all import values (in millions of dollars) for each year. 
The trend provides a clear starting point for understanding how U.S. food imports have grown and fluctuated over time, 
forming the baseline context for deeper analyses by category and country in later visuals.
"""

chart_1 = (
    alt.Chart(df_clean)
    .mark_line(point=True)
    .encode(
        x=alt.X("YearNum:O", title="Year"), 
        y=alt.Y("sum(FoodValue):Q", title="Total Import Value (Million $)"))
    .properties(title="Total Food Imports Over Time")
)

chart_1

alt.Chart(...)

In [4]:
"""
Visualization 2: Changing Composition of U.S. Food Imports by Category

This stacked percentage area chart visualizes how the composition of U.S. food imports has evolved over time across all available categories. 
Each band represents a category’s share of total imports in a given year, with the height normalized to 100%.

The inclusion of all categories highlights the broad diversity of imported food products—from animal and plant commodities to processed goods and specialty items. 
While some categories maintain a relatively stable share, others fluctuate substantially across the years, revealing shifts in consumer demand, production costs, and trade policies.

The chart uses a non-default color palette to help differentiate overlapping regions and draw attention to structural changes rather than year-to-year noise. 
This visualization builds directly on the overall trend in Visualization 1, adding context about what kinds of goods are driving the long-term increase in import value.
"""

chart_2 = (
    alt.Chart(df_clean)
    .mark_area()
    .encode(
        x=alt.X("YearNum:O", title="Year"),
        y=alt.Y("sum(FoodValue):Q", title="Total Import Value (Million $)", stack="normalize"),
        color=alt.Color("Category:N", title="Category", scale=alt.Scale(scheme="tableau10"))
    )
    .properties(
        title="Changing Composition of U.S. Food Imports by Category (%)",
    )
)

chart_2

alt.Chart(...)

In [5]:
"""
Visualization 3: Top Food-Exporting Countries to the U.S. (All Years)

This horizontal bar chart ranks the eight countries that have cumulatively exported the most food to the United States across all available years. 
Each bar’s length reflects the total import value in millions of dollars. 
Canada and Mexico lead the list by a large margin, followed by other major suppliers such as China.

The horizontal layout and color-coded bars make cross-country comparisons straightforward, while limiting the display to the top eight ensures clarity without losing key context about the U.S.’s major long-term trading partners.
"""

df_country_totals = (
    df_clean
    .group_by("Country")
    .agg(pl.sum("FoodValue").alias("TotalImports"))
    .sort("TotalImports", descending=True)
)

df_top8 = df_country_totals.head(8)

chart_3a = (
    alt.Chart(df_top8)
    .mark_bar()
    .encode(
    x=alt.X("Country:N", sort='-y', title="Country"),
    y=alt.Y("TotalImports:Q", title="Total Food Imports (Million $)"),
    color=alt.Color("Country:N", legend=None, scale=alt.Scale(scheme="tableau10"))
    )
    .properties(title='Top Importing Countries')
)
chart_3a

alt.Chart(...)

In [6]:
chart_3b = (
    alt.Chart(df_top8)
    .mark_bar()
    .encode(
        x=alt.X("TotalImports:Q", title="Total Food Imports (Million $)"),
        y=alt.Y('Country:N', sort='-x', title='Country'),
        color=alt.Color('Country:N', legend=None, scale=alt.Scale(scheme="tableau10"))
    )
    .properties(title='Top Importing Countries')
)

chart_3b

alt.Chart(...)

In [7]:
"""
Visualization 4: Canada vs. Mexico: Comparing U.S. Food Import Trends

This visualization isolates the two largest U.S. food import partners — Canada and Mexico — to examine how their contributions have changed over time.
The chart shows that both countries exhibit steady growth in export value to the U.S..
The dual-line comparison reinforces the geographic concentration seen in earlier charts while hinting at differing growth dynamics between the two neighbors.
"""

df_can_mex = (
    df_clean
    .filter(pl.col("Country").is_in(["CANADA", "MEXICO"]))
    .group_by(["YearNum", "Country"])
    .agg(pl.sum("FoodValue").alias("TotalImports"))
    .sort(["Country", "YearNum"])
)

chart_4 = (
    alt.Chart(df_can_mex)
    .mark_line(point=True)
    .encode(
        x=alt.X("YearNum:O", title="Year"),
        y=alt.Y("TotalImports:Q", title="Total Import Value (Million $)"),
        color=alt.Color("Country:N", title="Country", scale=alt.Scale(domain=["CANADA", "MEXICO"], range=["#377eb8", "#ff7f00"])),
    )
    .properties(
        title="Canada vs Mexico: U.S. Food Import Trends Over Time",
    )
)

chart_4

alt.Chart(...)

In [8]:
"""
Visualization 5: Heatmap: Category-Level Import Intensity

This heatmap visualizes how the value of U.S. food imports changed across categories and years.
Darker cells indicate higher import volumes, revealing structural shifts.
The visual highlights how diversification in imported foods has grown alongside globalization and trade liberalization.

"""
df_heatmap = (
    df_clean
    .group_by(["Category", "YearNum"])
    .agg(pl.sum("FoodValue").alias("TotalValue"))
    .sort(["Category", "YearNum"])
)

chart_5 = (
    alt.Chart(df_heatmap)
    .mark_rect()
    .encode(
        x=alt.X("YearNum:O", title="Year"),
        y=alt.Y("Category:N", title="Category"),
        color=alt.Color(
            "TotalValue:Q",
            title="Total Imports ($M)",
            scale=alt.Scale(scheme="yellowgreenblue")
        )
    )
    .properties(
        title="U.S. Food Import Intensity by Category and Year",
    )
)

chart_5

alt.Chart(...)

In [9]:
"""
Visualization 6: Treemap of Canada’s Exports to the U.S.

This visualization decomposes Canada’s food exports to the United States into their underlying product categories and commodities. 
Each rectangle’s size represents the total import value, with darker tones denoting higher volumes.
The treemap reveals that Canada’s largest contributions come from Meats and Grains, followed by Dairy and Beverages. 
The visualization highlights how trade relationships are concentrated in specific commodity clusters, reflecting Canada’s strong agricultural export sectors and North American supply-chain integration.
"""

df_canada = (
    df_clean
    .filter(pl.col("Country") == "CANADA")
    .group_by(["Category", "Commodity"])
    .agg(pl.sum("FoodValue").alias("TotalValue"))
    .sort("TotalValue", descending=True)
)

df_canada_top10 = (
    df_canada
    .sort("TotalValue", descending=True)
    .head(10)
)

chart_6a = (
    alt.Chart(df_canada_top10)
    .mark_rect(stroke="white")
    .encode(
        x=alt.X("Category:N", sort=None, title="Category"),
        y=alt.Y("Commodity:N", sort=None, title="Commodity"),
        color=alt.Color("TotalValue:Q",
                        title="Import Value ($M)",
                        scale=alt.Scale(scheme="tealblues"))
    )
    .properties(
        title="Composition of U.S. Food Imports from Canada by Commodity",
    )
)
chart_6a


alt.Chart(...)

In [10]:
df_mexico = (
    df_clean
    .filter(pl.col("Country") == "MEXICO")
    .group_by(["Category", "Commodity"])
    .agg(pl.sum("FoodValue").alias("TotalValue"))
    .sort("TotalValue", descending=True)
)

df_mexico_top10 = (
    df_mexico
    .sort("TotalValue", descending=True)
    .head(10)
)

chart_6b = (
    alt.Chart(df_mexico_top10)
    .mark_rect(stroke="white")
    .encode(
        x=alt.X("Category:N", sort=None, title="Category"),
        y=alt.Y("Commodity:N", sort=None, title="Commodity"),
        color=alt.Color("TotalValue:Q",
                        title="Import Value ($M)",
                        scale=alt.Scale(scheme="tealblues"))
    )
    .properties(
        title="Composition of U.S. Food Imports from Mexico by Commodity",
    )
)
chart_6b

alt.Chart(...)

In [11]:
"""
Visualization 7: Momentum of U.S. Food Import Categories Over Time

This visualization replaces the faceted small-multiples view with a motion-based trail plot that 
emphasizes the intensity and trajectory of import growth across categories. 
Each line’s thickness represents the magnitude of total imports in a given year, 
creating a visual sense of "momentum" that highlights both scale and trend simultaneously.

Compared to earlier visualizations, this design conveys not only direction (upward or downward) 
but also relative strength — thicker trails show where imports expanded most aggressively. 
For example, large trails for categories such as Meats or Grains indicate dominant and sustained growth,
while thinner, more fluctuating paths represent smaller or more volatile sectors.

I chose this chart type because it visually balances readability with motion, making 
structural differences across categories feel dynamic rather than static. 
It complements the earlier stacked area chart by shifting the focus from composition (shares) 
to movement (change velocity), reinforcing the story of accelerating U.S. food import demand.
"""


chart_7 = (
    alt.Chart(df_clean)
    .mark_trail()
    .encode(
        x=alt.X("YearNum:O", title="Year"),
        y=alt.Y("sum(FoodValue):Q", title="Total Import Value (Million $)"),
        size=alt.Size("sum(FoodValue):Q", legend=None),
        color=alt.Color("Category:N", title="Category", scale=alt.Scale(scheme="tableau20")),
    )
    .properties(title="Momentum of U.S. Food Import Categories Over Time")
)

chart_7

alt.Chart(...)